In [ ]:
%matplotlib inline


# Make a Rectangular AWG

This simple example illustrates how to make a rectangular AWG and how to run a Caphe simulation on it.
For this example, we use the Luceda AWG Designer module.

## Getting started

We start by importing the technology with other required modules:


In [ ]:
from si_fab import all as pdk  # noqa
from ipkiss3 import all as i3
import numpy

import awg_designer.all as awg
from si_fab_awg import all as awg_pdk

Next, create a template for the free propagation region.
This defines the layers, slab modes, etc.



In [ ]:
slab_t = awg_pdk.SiSlabTemplate()
slab_t.Layout()
slab_t.SlabModes(modes=[awg.SimpleSlabMode(name="TE0", n_eff=2.8, n_g=3.2, polarization="TE")])

N = 44  # number of arms
R = 150.0  # radius of the star couplers
W = 2.0  # aperture width
M = 8  # outputs

## The aperture

Make a virtual aperture



In [ ]:
ap = awg_pdk.SiRibAperture(
    slab_template=slab_t,
    aperture_core_width=W,
    aperture_cladding_width=1.0,
)
ap_lo = ap.Layout()
ap_sm = ap.FieldModelFromCamfr()
ap_cm = ap.CircuitModel(simulation_wavelengths=[1.55])

## The input star coupler

Make a multi-aperture for the arms consisting of N apertures like these, arranged in a circle
and get the transformations of the individual apertures.



In [ ]:
angle_step = i3.RAD2DEG * (W + 0.2) / R
angles_arms = numpy.linspace(-angle_step * (N - 1) / 2.0, angle_step * (N - 1) / 2.0, N)
ap_arms_in, _, trans_arms_in, trans_ports_in = awg.get_star_coupler_apertures(
    apertures_arms=[ap] * N,
    apertures_ports=[ap],
    angles_arms=angles_arms,
    angles_ports=[0],
    radius=R,
    mounting="confocal",
    input=True,
)

Make the input star coupler



In [ ]:
sc_in = awg.StarCoupler(aperture_in=ap, aperture_out=ap_arms_in)

sc_in_lo = sc_in.Layout(
    contour=awg.get_star_coupler_extended_contour(
        apertures_in=[ap],
        apertures_out=[ap] * N,
        trans_in=trans_ports_in,
        trans_out=trans_arms_in,
        radius_in=R,
        radius_out=R,
        extension_angles=(10, 5),
    )
)
sc_in_lo.visualize()

## The output star coupler

Make the multi-apertures for the outputs and get the transformations for the individual apertures.



In [ ]:
angle_step = i3.RAD2DEG * (4.7) / R
angles_ports = numpy.linspace(angle_step * (M - 1) / 2.0, -angle_step * (M - 1) / 2.0, M)
ap_arms_out, ap_out, trans_arms_out, trans_ports_out = awg.get_star_coupler_apertures(
    apertures_arms=[ap] * N,
    apertures_ports=[ap] * M,
    angles_arms=angles_arms,
    angles_ports=angles_ports,
    radius=R,
    mounting="rowland",
    input=False,
)

Make the output star coupler



In [ ]:
sc_out = awg.StarCoupler(aperture_in=ap_arms_out, aperture_out=ap_out)
sc_out_lo = sc_out.Layout(
    contour=awg.get_star_coupler_extended_contour(
        apertures_in=[ap] * N,
        apertures_out=[ap] * M,
        trans_in=trans_arms_out,
        trans_out=trans_ports_out,
        radius_in=R,
        radius_out=R / 2,
        extension_angles=(10, 10),
    )
)
sc_out_lo.visualize()

## The rectangular waveguide array



Make the :py:class:`RectangularWaveguideArray <awg_designer.all.RectangularWaveguideArray>`



In [ ]:
delays = [50.0 * i for i in range(N)]
ports = [port for port in sc_in_lo.ports.y_sorted() if "out" in port.name]
waveguide_array = awg.RectangularWaveguideArray(start_ports=ports, delay_lengths=delays)
waveguide_array.Layout(bundle_spacing=40)

## The Arrayed Waveguide Grating

Make an AWG with the 3 building blocks



In [ ]:
rect_awg = awg.ArrayedWaveguideGrating(
    star_coupler_in=sc_in,
    star_coupler_out=sc_out,
    waveguide_array=waveguide_array,
)

awg_lo = rect_awg.Layout()
awg_lo.visualize()

## Running the Caphe simulation



In [ ]:
print("Running Caphe simulation (with wavelength-independent star couplers)")
sc_in.CircuitModel(simulation_wavelengths=[1.55])
sc_out.CircuitModel(simulation_wavelengths=[1.55])
awg_cm = rect_awg.CircuitModel()
wavelengths = numpy.linspace(1.52, 1.58, 401)

import time  # noqa

t0 = time.time()
S = awg_cm.get_smatrix(wavelengths)
print("Calculation time:", time.time() - t0)

term_pairs = [("in1", f"out{i}") for i in range(1, M + 1)]
S.visualize(term_pairs=term_pairs, scale="dB")

## Using SpectrumAnalyzer to analyze the results
We finally use :py:class:`i3.SpectrumAnalyzer <ipkiss3.all.SpectrumAnalyzer>` to
detect the peaks and calculate the crosstalk.



In [ ]:
sa = i3.SpectrumAnalyzer(
    smatrix=S,
    input_port_mode="in1",
    output_port_modes=[f"out{i}" for i in range(1, M + 1)],
    peak_method="cwt",
    peak_threshold=-25,
)
sa.visualize(title="Peaks")

Let's calculate the passbands for a cutoff of 25 dB:



In [ ]:
bands = sa.cutoff_passbands(-25)

And then calculate the nearest neighbor crosstalk for each channel.
The value reported for `out1` is the crosstalk caused by the neirest channels `out8` and `out2`:



In [ ]:
print(sa.near_crosstalk(bands))

We also calculate the far neighbor crosstalk, which ignores nearest neighbors:



In [ ]:
print(sa.far_crosstalk(bands))